In [1]:
!pip install flask-ngrok

In [3]:
import spacy
import random
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import networkx as nx
import os
import gensim
from gensim.test.utils import datapath, get_tmpfile
from gensim.models import KeyedVectors
from gensim.scripts.glove2word2vec import glove2word2vec

model = KeyedVectors.load_word2vec_format('/content/drive/My Drive/Neural Question Generator/Embeddings/word2vec.txt')
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
nlp = spacy.load('en_core_web_sm')

/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:252: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL


In [4]:
def text_summarizer(text):
  list_sent = []
  doc = nlp(text)
  for sent in doc.sents:
    list_sent.append(str(sent))
  num_sent = len(list_sent)
  list_embed = []
  for sent in list_sent:
    doc_sent = nlp(sent)
    list_embed.append(doc_sent.vector.reshape(1,96))
  similarity = np.zeros([num_sent, num_sent])
  for i in range(num_sent):
    for j in range(num_sent):
      similarity[i][j] = cosine_similarity(list_embed[i], list_embed[j])[0][0]
  nx_graph = nx.from_numpy_array(similarity)
  scores = nx.pagerank(nx_graph)
  ranked_sentences = sorted(((scores[i],s) for i,s in enumerate(list_sent)), reverse=True)
  sentences = []
  for score, sent in ranked_sentences:
    sentences.append(sent)
  return sentences  

def distractor_generator(word):
  word = word.lower()
  if(word in model.wv.vocab):
    similar = model.most_similar(positive=[word],topn=3)
    ans = []
    for tup in similar:
      ans.append(tup[0])
    return ans
  else:
    return []

def ireplace(old, new, text):
    index_l = text.lower().index(old.lower())
    return text[:index_l] + new + text[index_l + len(old):]

def return_question_with_answer(text):
  try:
    text = str(text).replace('\n',' ')
    doc = nlp(text)
    if(len(doc.ents)>0):
      ans = str(random.choice(doc.ents))
      ques = ireplace(ans, '_______',text)
      return ques, ans
    else:
      print("No entities")
      return -1, -1
  except:
    return -1,-1

In [ ]:
from flask_ngrok import run_with_ngrok
from flask import Flask, jsonify, request
app = Flask(__name__)
run_with_ngrok(app)   

@app.route("/", methods=['GET', 'POST'])
def home():
  data = request.json
  text = data['text']
  print(text)
  questions = []
  summary = text_summarizer(text)
  count = 1
  for sent in summary:
    ques, ans = return_question_with_answer(sent)
    if(ques!=-1):
      distractors = distractor_generator(ans)
      if(len(distractors)>0):
        distractors.append(ans)
        dictionary = {
            "_id": count,
            "question": ques,
            "correct": ans.lower(),
            "options": distractors
        }
        count = count+1
        questions.append(dictionary)
  print(questions)
  
  return jsonify({
      "questions": questions
  })
app.run()

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:5000/ (Press CTRL+C to quit)


 * Running on http://bfec80809869.ngrok.io
 * Traffic stats available on http://127.0.0.1:4040
George Walker Bush (born July 6, 1946) is an American politician and businessman who served as the 43rd president of the United States from 2001 to 2009. A member of the Republican Party, he had previously served as the 46th governor of Texas from 1995 to 2000. Born into the Bush family, his father, George H. W. Bush, served as the 41st president of the United States from 1989 to 1993. Bush is the eldest son of Barbara and George H. W. Bush. As such he is the second son of a former United States President to himself become the American president, with the first being John Quincy Adams. He flew warplanes in the Texas and Alabama Air National Guard. After graduating from Yale College in 1968 and Harvard Business School in 1975, he worked in the oil industry. Bush married Laura Welch in 1977 and unsuccessfully ran for the U.S. House of Representatives shortly thereafter. He later co-owned the Te

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:25: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):
127.0.0.1 - - [10/Oct/2020 14:31:05] "POST / HTTP/1.1" 200 -


[{'_id': 1, 'question': '_______ was elected president of the United States in 2000 when he defeated Democratic incumbent Vice President Al Gore after a narrow and contested win that involved a Supreme Court decision to stop a recount in Florida.', 'correct': 'bush', 'options': ['clinton', 'obama', 'barack', 'Bush']}, {'_id': 2, 'question': 'Born into the Bush family, his father, George H. W. Bush, served as the _______ president of the United States from 1989 to 1993.', 'correct': '41st', 'options': ['39th', '38th', '48th', '41st']}, {'_id': 3, 'question': 'In _______, Bush ordered an invasion of Iraq, with the administration arguing that the Saddam Hussein regime possessed an active weapons of mass destruction (WMD) program, and that the Iraqi government posed a threat to the United States.', 'correct': '2003', 'options': ['2002', '2001', '2005', '2003']}, {'_id': 4, 'question': 'A member of the Republican Party, he had previously served as the _______ governor of Texas from 1995 to 

...

[{'_id': 1, 'question': "In response to the September 11 terrorist attacks, _______ created the United States Department of Homeland Security and launched a 'War on Terror' that began with the war in Afghanistan in 2001.", 'correct': 'bush', 'options': ['clinton', 'obama', 'barack', 'Bush']}, {'_id': 2, 'question': 'In _______, Bush ordered an invasion of Iraq, with the administration arguing that the Saddam Hussein regime possessed an active weapons of mass destruction (WMD) program, and that the Iraqi government posed a threat to the United States.', 'correct': '2003', 'options': ['2002', '2001', '2005', '2003']}, {'_id': 3, 'question': 'A member of the Republican Party, he had previously served as the 46th governor of _______ from 1995 to 2000.', 'correct': 'texas', 'options': ['arizona', 'florida', 'kansas', 'Texas']}, {'_id': 4, 'question': 'Bush also helped make _______ the leading producer of wind powered electricity in the United States.', 'correct': 'texas', 'options': ['arizo

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:25: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):
127.0.0.1 - - [10/Oct/2020 18:14:10] "POST / HTTP/1.1" 200 -


[{'_id': 1, 'question': 'In 2003, Bush ordered an invasion of _______, with the administration arguing that the Saddam Hussein regime possessed an active weapons of mass destruction (WMD) program, and that the Iraqi government posed a threat to the United States.', 'correct': 'iraq', 'options': ['afghanistan', 'iraqi', 'lebanon', 'Iraq']}, {'_id': 2, 'question': 'A member of the Republican Party, he had previously served as the 46th governor of _______ from 1995 to 2000.', 'correct': 'texas', 'options': ['arizona', 'florida', 'kansas', 'Texas']}, {'_id': 3, 'question': '_______ also helped make Texas the leading producer of wind powered electricity in the United States.', 'correct': 'bush', 'options': ['clinton', 'obama', 'barack', 'Bush']}, {'_id': 4, 'question': 'Bush also passed the _______ Modernization Act, which created Medicare Part D, and funding for the AIDS relief program known as PEPFAR.', 'correct': 'medicare', 'options': ['medicaid', 'beneficiaries', 'pension', 'Medicare']

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:25: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):
127.0.0.1 - - [10/Oct/2020 18:14:18] "POST / HTTP/1.1" 200 -


[{'_id': 1, 'question': 'Bush was elected president of the United States in 2000 when he defeated _______ incumbent Vice President Al Gore after a narrow and contested win that involved a Supreme Court decision to stop a recount in Florida.', 'correct': 'democratic', 'options': ['republican', 'democrats', 'party', 'Democratic']}, {'_id': 2, 'question': "In response to the September 11 terrorist attacks, _______ created the United States Department of Homeland Security and launched a 'War on Terror' that began with the war in Afghanistan in 2001.", 'correct': 'bush', 'options': ['clinton', 'obama', 'barack', 'Bush']}, {'_id': 3, 'question': 'In _______, Bush ordered an invasion of Iraq, with the administration arguing that the Saddam Hussein regime possessed an active weapons of mass destruction (WMD) program, and that the Iraqi government posed a threat to the United States.', 'correct': '2003', 'options': ['2002', '2001', '2005', '2003']}, {'_id': 4, 'question': 'A member of the Repub

In [ ]:
def textrank_summarizer(text, num_sent):
  doc = nlp(text)
  sentence_list = []
  for sent in doc.sents:
    sentence_list.append(sent)
  sentences = []
  for sent in doc.sents:
    doc1 = nlp(str(sent))
    sentence = [str(token) for token in doc1]
    sentences.append(sentence)
  with tf.Session() as sess:
    sess.run([tf.global_variables_initializer(), tf.tables_initializer()])
    embeddings = sess.run(embed(sentences[0]))
  embeddings = []
  with tf.Session() as sess:
    sess.run([tf.global_variables_initializer(), tf.tables_initializer()])
    for sentence in sentences:
      embeddings.append(sess.run(embed(sentence)))
  average_embedding = []
  for embedding in embeddings:
    average = np.zeros(512)
    length = len(embeddings)
    for word_embedding in embedding:
      average = average+word_embedding
    average = average/length
    average_embedding.append(average)
  average_embedding = np.array(average_embedding)
  sim_mat = np.zeros([length, length])
  for i in range(length):
    for j in range(length):
      if i != j:
        sim_mat[i][j] = cosine_similarity(average_embedding[i].reshape(1,512), average_embedding[j].reshape(1,512))[0,0]
  nx_graph = nx.from_numpy_array(sim_mat)
  scores = nx.pagerank(nx_graph)
  ranked_sentences = sorted(((scores[i],s) for i,s in enumerate(sentence_list)), reverse=True)
  final_summary = [ranked_sentences[i][1] for i in range(num_sent)]
  return final_summary

In [ ]:
text = """The Third Battle of Panipat took place on 14 January 1761 at Panipat, about 97 km (60 miles) north of Delhi, between the Maratha Empire and the invading Afghan army of the King of Afghans, Ahmad Shah Abdali, supported by three Indian allies — the Rohilla Najib-ud-daulah, Afghans of the Doab region, and Shuja-ud-Daula, the Nawab of Awadh. The Maratha army was led by Sadashivrao Bhau who was third in authority after the Chhatrapati (Maratha King) and the Peshwa (Maratha Prime Minister). The main Maratha army was stationed in Deccan with the Peshwa. Militarily, the battle pitted the artillery and cavalry of the Marathas against the heavy cavalry and mounted artillery (zamburak and jezail) of the Afghans and Rohillas led by Abdali and Najib-ud-Daulah, both ethnic Afghans. The battle is considered one of the largest and most eventful fought in the 18th century,[10] and it has perhaps the largest number of fatalities in a single day reported in a classic formation battle between two armies. The specific site of the battle itself is disputed by historians, but most consider it to have occurred somewhere near modern-day Kaalaa Aamb and Sanauli Road. The battle lasted for several days and involved over 125,000 troops. Protracted skirmishes occurred, with losses and gains on both sides. The forces led by Ahmad Shah Durrani came out victorious after destroying several Maratha flanks. The extent of the losses on both sides is heavily disputed by historians, but it is believed that between 60,000–70,000 were killed in fighting, while the numbers of injured and prisoners taken vary considerably. According to the single best eyewitness chronicle—the bakhar by Shuja-ud-Daulah's Diwan Kashi Raj—about 40,000 Maratha prisoners were slaughtered in cold blood the day after the battle.[9] Grant Duff includes an interview of a survivor of these massacres in his History of the Marathas and generally corroborates this number. Shejwalkar, whose monograph Panipat 1761 is often regarded as the single best secondary source on the battle, says that 'not less than 100,000 Marathas (soldiers and non-combatants) perished during and after the battle.'"""

In [ ]:
carbon_text = """    Carbon gets its name from the Latin word carbo, which means "coal." Diamonds and graphite are among the hardest and softest natural materials known, respectively. The only difference between the two is their crystal structure.Carbon makes up 0.032 percent of the Earth's lithosphere (crust and outer mantle) by weight, according to the Encyclopedia of Earth. A rough estimate of the weight of the lithosphere by La Salle University geologist David Smith is 300,000,000,000,000,000,000,000 (or 3*10^23) pounds, making the approximate weight of carbon in the lithosphere 10,560,000,000,000,000,000,000 (or 1.056*10^22) pounds. Carbon dioxide (a carbon atom plus two oxygen atoms) makes up about 0.04 percent of Earth's atmosphere, according to the National Oceanic & Atmospheric Administration (NOAA) — an increase over pre-industrial times, because of the burning of fossil fuels. Carbon monoxide (a carbon atom plus one oxygen atom) is an odorless gas produced from the burning of fossil fuels. Carbon monoxide kills by binding to hemoglobin, the oxygen-carrying compound in the blood. Carbon monoxide bonds to hemoglobin 210 times more strongly than oxygen binds to hemoglobin, effectively crowding out oxygen and suffocating the tissues, according to a 2001 paper in the Journal of the Royal Society of Medicine. Diamond, the flashiest version of carbon, is formed under great pressure deep in the Earth's crust. The largest gem-quality diamond ever found was the Cullinan diamond, which was discovered in 1905, according to the Royal Collection Trust. The uncut diamond was 3,106.75 carats. The largest gem cut from the stone, at 530.2 carats, is one of the Crown Jewels of the United Kingdom and is known as the Great Star of Africa. The tattoos of Ötzi the Iceman, a 5,300-year-old corpse found frozen in the Alps, were inked from carbon, according to a 2009 study in the Journal of Archaeological Science. Small incisions in the skin were made, and charcoal rubbed in, perhaps as part of an acupuncture treatment."""

In [ ]:
text = """The Taj Mahal is an ivory-white marble mausoleum on the southern bank of the river Yamuna in the Indian city of Agra. It was commissioned in 1632 by the Mughal emperor Shah Jahan (reigned from 1628 to 1658) to house the tomb of his favourite wife, Mumtaz Mahal; it also houses the tomb of Shah Jahan himself. The tomb is the centrepiece of a 17-hectare (42-acre) complex, which includes a mosque and a guest house, and is set in formal gardens bounded on three sides by a crenellated wall. Construction of the mausoleum was essentially completed in 1643, but work continued on other phases of the project for another 10 years. The Taj Mahal complex is believed to have been completed in its entirety in 1653 at a cost estimated at the time to be around 32 million rupees, which in 2020 would be approximately 70 billion rupees (about U.S. $916 million). The construction project employed some 20,000 artisans under the guidance of a board of architects led by the court architect to the emperor, Ustad Ahmad Lahauri. The Taj Mahal was designated as a UNESCO World Heritage Site in 1983 for being "the jewel of Muslim art in India and one of the universally admired masterpieces of the world's heritage". It is regarded by many as the best example of Mughal architecture and a symbol of India's rich history. The Taj Mahal attracts 7–8 million visitors a year and in 2007, it was declared a winner of the New 7 Wonders of the World (2000–2007) initiative."""

In [ ]:
carbon_text

'    Carbon gets its name from the Latin word carbo, which means "coal." Diamonds and graphite are among the hardest and softest natural materials known, respectively. The only difference between the two is their crystal structure.Carbon makes up 0.032 percent of the Earth\'s lithosphere (crust and outer mantle) by weight, according to the Encyclopedia of Earth. A rough estimate of the weight of the lithosphere by La Salle University geologist David Smith is 300,000,000,000,000,000,000,000 (or 3*10^23) pounds, making the approximate weight of carbon in the lithosphere 10,560,000,000,000,000,000,000 (or 1.056*10^22) pounds. Carbon dioxide (a carbon atom plus two oxygen atoms) makes up about 0.04 percent of Earth\'s atmosphere, according to the National Oceanic & Atmospheric Administration (NOAA) — an increase over pre-industrial times, because of the burning of fossil fuels. Carbon monoxide (a carbon atom plus one oxygen atom) is an odorless gas produced from the burning of fossil fuels

In [ ]:
summary = textrank_summarizer(text, 5)

In [ ]:
summary

[The Taj Mahal was designated as a UNESCO World Heritage Site in 1983 for being "the jewel of Muslim art in India and one of the universally admired masterpieces of the world's heritage".,
 The Taj Mahal attracts 7–8 million visitors a year and in 2007, it was declared a winner of the New 7 Wonders of the World (2000–2007) initiative.,
 The tomb is the centrepiece of a 17-hectare (42-acre) complex, which includes a mosque and a guest house, and is set in formal gardens bounded on three sides by a crenellated wall.,
 Construction of the mausoleum was essentially completed in 1643, but work continued on other phases of the project for another 10 years.,
 It was commissioned in 1632 by the Mughal emperor Shah Jahan (reigned from 1628 to 1658) to house the tomb of his favourite wife, Mumtaz Mahal; it also houses the tomb of Shah Jahan himself.]

In [ ]:
def ireplace(old, new, text):
    index_l = text.lower().index(old.lower())
    return text[:index_l] + new + text[index_l + len(old):]

In [ ]:
def ireplace(old, new, text):
    index_l = text.lower().index(old.lower())
    return text[:index_l] + new + text[index_l + len(old):]

def return_question_with_answer(text):
  try:
    text = str(text).replace('\n',' ')
    doc = nlp(text)
    if(len(doc.ents)>0):
      ans = str(random.choice(doc.ents))
      ques = ireplace(ans, '_______',text)
      return ques, ans
    else:
      print("No entities")
      return -1, -1
  except:
    return -1,-1

In [ ]:
return_question_with_answer(summary[0])

('The Taj Mahal was designated as a UNESCO World Heritage Site in 1983 for being "the jewel of _______ art in India and one of the universally admired masterpieces of the world\'s heritage".',
 'Muslim')

In [ ]:
def distractor_generator(word):
  word = word.lower()
  if(word in model.wv.vocab):
    similar = model.most_similar(positive=[word],topn=3)
    ans = []
    for tup in similar:
      ans.append(tup[0])
    return ans
  else:
    return []

In [ ]:
def print_questions_with_answers(summary):
  ctr = 0
  for i in range(len(summary)):
    question, answer = return_question_with_answer(summary[i])
    if(question!=-1):
      choices = distractor_generator(answer)
      if(len(choices)>0):
        print('Q',(ctr+1),': ',question)
        choices.append(answer)
        random.shuffle(choices)
        print("A.", choices[0], "\tB:", choices[1],"\tC:", choices[2], "\tD:", choices[3])
        print('Answer: ', answer)
        ctr = ctr+1

In [ ]:
print_questions_with_answers(summary)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  This is separate from the ipykernel package so we can avoid doing imports until
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


Q 1 :  Diamond, the flashiest version of carbon, is formed under great pressure deep in the _______'s crust.
A. planet 	B: Earth 	C: mars 	D: space
Answer:  Earth
Q 2 :  Carbon dioxide (a carbon atom plus _______ oxygen atoms) makes up about 0.04 percent of Earth's atmosphere, according to the National Oceanic & Atmospheric Administration (NOAA) — an increase over pre-industrial times, because of the burning of fossil fuels.
A. four 	B: five 	C: two 	D: three
Answer:  two
Q 3 :  The tattoos of Ötzi the Iceman, a 5,300-year-old corpse found frozen in the _______, were inked from carbon, according to a 2009 study in the Journal of Archaeological Science.
A. alpine 	B: Alps 	C: dinaric 	D: pyrenees
Answer:  Alps
No entities
Q 4 :  Carbon monoxide bonds to hemoglobin 210 times more strongly than oxygen binds to hemoglobin, effectively crowding out oxygen and suffocating the tissues, according to a _______ paper in the Journal of the Royal Society of Medicine.
A. 2002 	B: 2003 	C: 2001 	D: 

NameError: ignored

In [ ]:
summary

[Shejwalkar, whose monograph Panipat 1761 is often regarded as the single best secondary source on the battle, says that 'not less than 100,000 Marathas (soldiers and non-combatants) perished during and after the battle.',
 According to the single best eyewitness chronicle—the bakhar by Shuja-ud-Daulah's Diwan Kashi Raj—about 40,000 Maratha prisoners were slaughtered in cold blood the day after the battle.[9],
 Militarily, the battle pitted the artillery and cavalry of the Marathas against the heavy cavalry and mounted artillery (zamburak and jezail) of the Afghans and Rohillas led by Abdali and Najib-ud-Daulah, both ethnic Afghans.,
 The battle is considered one of the largest and most eventful fought in the 18th century,[10] and it has perhaps the largest number of fatalities in a single day reported in a classic formation battle between two armies.,
 The specific site of the battle itself is disputed by historians, but most consider it to have occurred somewhere near modern-day Kaal

In [ ]:
doc = nlp(str(summary[2]))

In [ ]:
for chunk in doc.ents:
  print(chunk)

Shuja-ud-Daulah's
Diwan Kashi Raj
about 40,000
Maratha
the day


In [ ]:
ireplace(str(random.choice(doc.ents)), '_______', str(summary[2]))

'Militarily, the battle pitted the artillery and cavalry of the Marathas against the heavy cavalry and mounted artillery (zamburak and jezail) of the Afghans and _______ led by Abdali and Najib-ud-Daulah, both ethnic Afghans.'

In [ ]:
print_questions_with_answers(summary)

Q 1 :  Shejwalkar, whose monograph Panipat _______ is often regarded as the single best secondary source on the battle, says that 'not less than 100,000 Marathas (soldiers and non-combatants) perished during and after the battle.'
Answer:  1761
Q 2 :  According to the single best eyewitness chronicle—the bakhar by Shuja-ud-Daulah's Diwan Kashi Raj—about 40,000 _______ prisoners were slaughtered in cold blood the day after the battle.[9]
Answer:  Maratha
Q 3 :  Militarily, the battle pitted the artillery and cavalry of the Marathas against the heavy cavalry and mounted artillery (zamburak and jezail) of the _______ and Rohillas led by Abdali and Najib-ud-Daulah, both ethnic Afghans.
Answer:  Afghans
Q 4 :  The battle is considered one of the largest and most eventful fought in the 18th century,[10] and it has perhaps the largest number of fatalities in _______ reported in a classic formation battle between two armies.
Answer:  a single day
Q 5 :  The specific site of the battle itself i

In [ ]:
print_questions_with_answers(summary)

Q 1 :  Shejwalkar, whose monograph Panipat _______ is often regarded as the single best secondary source on the battle, says that 'not less than 100,000 Marathas (soldiers and non-combatants) perished during and after the battle.'
Answer:  1761
Q 2 :  According to the single best eyewitness chronicle—the bakhar by Shuja-ud-Daulah's _______—about 40,000 Maratha prisoners were slaughtered in cold blood the day after the battle.[9]
Answer:  Diwan Kashi Raj
Q 3 :  Militarily, the battle pitted the artillery and cavalry of the Marathas against the heavy cavalry and mounted artillery (zamburak and jezail) of the _______ and Rohillas led by Abdali and Najib-ud-Daulah, both ethnic Afghans.
Answer:  Afghans
Q 4 :  The battle is considered one of the largest and most eventful fought in the 18th century,[10] and it has perhaps the largest number of fatalities in a single day reported in a classic formation battle _______.
Answer:  between two armies
Q 5 :  The specific site of the battle itself i

In [ ]:
from gensim.models import Word2Vec, KeyedVectors
from gensim.test.utils import datapath

In [ ]:
from gensim.test.utils import common_texts, get_tmpfile
from gensim.models import Word2Vec


In [ ]:
fname = get_tmpfile('/content/drive/My Drive/Neural Question Generator/Embeddings/glove.6B.50d.txt')

In [ ]:
model = Word2Vec.load_word2vec_format

In [ ]:
from google.colab import files
files.upload()

Saving word2vec.txt to word2vec.txt


{'word2vec.txt': b"3000000 300\n</s> 0.001129 -0.000896 0.000319 0.001534 0.001106 -0.001404 -0.000031 -0.000420 -0.000576 0.001076 -0.001022 -0.000618 -0.000755 0.001404 -0.001640 -0.000633 0.001633 -0.001007 -0.001266 0.000652 -0.000416 -0.001076 0.001526 -0.000275 0.000140 0.001572 0.001358 -0.000832 -0.001404 0.001579 0.000254 -0.000732 -0.000105 -0.001167 0.001579 0.000656 -0.000660 0.000003 0.001129 0.000427 -0.000370 -0.001152 0.001266 -0.000004 0.000265 -0.000402 0.000141 -0.000034 0.000759 -0.000519 -0.000071 0.000603 -0.000507 -0.001625 -0.000437 -0.000992 -0.001221 -0.000322 0.000069 -0.001167 -0.000511 0.001411 0.000336 -0.000475 -0.001373 0.000366 -0.001442 -0.000607 0.000801 0.001129 -0.000835 -0.001160 0.000916 0.000523 -0.000328 0.001595 -0.001579 -0.000357 0.000496 0.001015 -0.001099 -0.000166 -0.000142 -0.000261 0.001259 0.000039 0.000169 -0.001030 0.001610 0.000629 0.000418 -0.001350 0.000349 0.001144 -0.001205 -0.001183 0.000950 0.000061 0.000011 -0.000668 0.001244 

In [ ]:
from gensim.test.utils import datapath, get_tmpfile
from gensim.models import KeyedVectors
from gensim.scripts.glove2word2vec import glove2word2vec

In [ ]:
glove2word2vec('/content/drive/My Drive/Neural Question Generator/Embeddings/glove.6B.50d.txt', 'word2vec.txt')

/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:410: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL


(400000, 50)

In [ ]:
model = KeyedVectors.load_word2vec_format('word2vec.txt')

/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:410: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL


In [ ]:
model.save('incorrect_answer_model.pkl')

/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:410: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL


In [ ]:
model.most_similar('single')

/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


[('double', 0.844563364982605),
 ('one', 0.7847537398338318),
 ('a', 0.7746918797492981),
 ('another', 0.7743384838104248),
 ('same', 0.7725595831871033),
 ('third', 0.7655076384544373),
 ('first', 0.7583229541778564),
 ('only', 0.7473124861717224),
 ('tracks', 0.7455034255981445),
 ('each', 0.7446153163909912)]

In [ ]:
model.most_similar(positive=['oxygen'])

/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


[('dioxide', 0.927760899066925),
 ('gases', 0.8950349688529968),
 ('greenhouse', 0.8866274952888489),
 ('co2', 0.8825781345367432),
 ('emissions', 0.8803396224975586),
 ('nitrogen', 0.8141229152679443),
 ('pollutants', 0.8011458516120911),
 ('emission', 0.7800530195236206),
 ('sulfur', 0.7745556235313416),
 ('hydrogen', 0.7690752148628235)]

In [ ]:
def distractor_generator(word):
  word = word.lower()
  if(word in model.wv.vocab):
    similar = model.most_similar(positive=[word],topn=3)
    ans = []
    for tup in similar:
      ans.append(tup[0])
    return ans
  else:
    return []

In [ ]:
distractor_generator('1000')

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  This is separate from the ipykernel package so we can avoid doing imports until
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


['1500', '3000', '5000']

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  This is separate from the ipykernel package so we can avoid doing imports until
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


['awful', 'sorry', 'terrible']

In [ ]:
!pip install flask-ngrok

from flask_ngrok import run_with_ngrok
from flask import Flask
app = Flask(__name__)
run_with_ngrok(app)   #starts ngrok when the app is run

@app.route("/")
def home():
    return func()

app.run()

In [ ]:
text = """Carbon is a chemical element with the symbol C and atomic number 6. It is nonmetallic and tetravalent—making four electrons available to form covalent chemical bonds. It belongs to group 14 of the periodic table. Carbon makes up only about 0.025 percent of Earth’s crust. Three isotopes occur naturally, 12C and 13C being stable, while 14C is a radionuclide, decaying with a half-life of about 5,730 years. Carbon is one of the few elements known since antiquity. Carbon is the 15th most abundant element in the Earth's crust, and the fourth most abundant element in the universe by mass after hydrogen, helium, and oxygen. Carbon's abundance, its unique diversity of organic compounds, and its unusual ability to form polymers at the temperatures commonly encountered on Earth enables this element to serve as a common element of all known life. It is the second most abundant element in the human body by mass (about 18.5%) after oxygen. The atoms of carbon can bond together in diverse ways, resulting in various allotropes of carbon. The best known allotropes are graphite, diamond, and buckminsterfullerene. The physical properties of carbon vary widely with the allotropic form. For example, graphite is opaque and black while diamond is highly transparent. Graphite is soft enough to form a streak on paper (hence its name, from the Greek verb "γράφειν" which means "to write"), while diamond is the hardest naturally occurring material known. Graphite is a good electrical conductor while diamond has a low electrical conductivity. Under normal conditions, diamond, carbon nanotubes, and graphene have the highest thermal conductivities of all known materials. All carbon allotropes are solids under normal conditions, with graphite being the most thermodynamically stable form at standard temperature and pressure. They are chemically resistant and require high temperature to react even with oxygen. The most common oxidation state of carbon in inorganic compounds is +4, while +2 is found in carbon monoxide and transition metal carbonyl complexes. The largest sources of inorganic carbon are limestones, dolomites and carbon dioxide, but significant quantities occur in organic deposits of coal, peat, oil, and methane clathrates. Carbon forms a vast number of compounds, more than any other element, with almost ten million compounds described to date, and yet that number is but a fraction of the number of theoretically possible compounds under standard conditions. For this reason, carbon has often been referred to as the "king of the elements"."""

In [ ]:
textrank_summarizer(text, 10)

AttributeError: ignored

In [ ]:
!pip install bert-embedding

     |████████████████████████████████| 29.6MB 155kB/s 
     |████████████████████████████████| 13.8MB 167kB/s 
     |████████████████████████████████| 215kB 38.5MB/s 
  Created wheel for gluonnlp: filename=gluonnlp-0.6.0-cp36-none-any.whl size=259917 sha256=91d1f946a3efe746429e9a2542444776fc63ad5434aed228f658424e61b1847f
  Stored in directory: /root/.cache/pip/wheels/ff/48/ac/a77c79aa416ba6dd7bf487f2280b0471034f66141617965914
Successfully built gluonnlp
ERROR: xarray 0.15.1 has requirement numpy>=1.15, but you'll have numpy 1.14.6 which is incompatible.
ERROR: umap-learn 0.4.6 has requirement numpy>=1.17, but you'll have numpy 1.14.6 which is incompatible.
ERROR: tifffile 2020.9.3 has requirement numpy>=1.15.1, but you'll have numpy 1.14.6 which is incompatible.
ERROR: tensorflow 1.15.0 has requirement numpy<2.0,>=1.16.0, but you'll have numpy 1.14.6 which is incompatible.
ERROR: tensorflow-probability 0.11.0 has requirement gast>=0.3.2, but you'll have gast 0.2.2 which is incompatibl

In [ ]:
from bert_embedding import BertEmbedding

In [ ]:
embedding = BertEmbedding()

Vocab file is not found. Downloading.


In [ ]:
!pip3 install fasttext

     |████████████████████████████████| 71kB 1.9MB/s 
  Created wheel for fasttext: filename=fasttext-0.9.2-cp36-cp36m-linux_x86_64.whl size=3019883 sha256=50be69d288cd3eef4d64f797a392498013f7fd7b9db02a7c5eafa952378147ac
  Stored in directory: /root/.cache/pip/wheels/98/ba/7f/b154944a1cf5a8cee91c154b75231136cc3a3321ab0e30f592
Successfully built fasttext


In [ ]:
import spacy

In [ ]:
nlp = spacy.load("en_core_web_sm")

In [ ]:
doc = nlp(text)

In [ ]:
doc.vector

array([ 0.04688577,  0.46488196, -0.15739007, -0.02145781,  1.8503714 ,
       -0.04302982,  0.72607154,  0.2002245 ,  0.84882957,  1.2046403 ,
       -0.4017068 ,  0.24403046, -0.30386823, -0.784344  , -1.03368   ,
       -0.35513827, -1.2034214 , -0.1705056 , -0.33773062, -0.2092561 ,
        0.90058166,  0.25193217, -0.24384773,  0.23037645, -0.5860117 ,
        0.9103783 , -0.772445  , -0.08483088,  0.6544829 , -0.72787476,
        0.32286686,  0.2505628 ,  0.01719699, -0.48151323, -0.2742508 ,
       -0.641548  ,  0.48300716, -1.0106283 , -0.99189836, -0.20577227,
        1.5779444 , -0.00676511, -0.5245864 , -1.6075684 , -0.07301325,
       -0.48096055,  0.08795266,  0.21878156, -1.1481216 ,  0.59250176,
        1.198236  , -0.6777911 , -0.47481668, -0.04153032, -1.8578554 ,
        0.55039275,  0.4576164 ,  0.85954994, -0.05545497,  0.416872  ,
        0.6721804 ,  0.07838222,  1.3300784 ,  0.4757361 ,  0.952676  ,
       -0.2154439 ,  0.6904441 , -1.2501159 ,  0.14480554,  0.72

In [ ]:
dictionary = {
    text: doc.vector
}

In [ ]:
dictionary["text"] = doc.vector

{'Carbon is a chemical element with the symbol C and atomic number 6. It is nonmetallic and tetravalent—making four electrons available to form covalent chemical bonds. It belongs to group 14 of the periodic table. Carbon makes up only about 0.025 percent of Earth’s crust. Three isotopes occur naturally, 12C and 13C being stable, while 14C is a radionuclide, decaying with a half-life of about 5,730 years. Carbon is one of the few elements known since antiquity. Carbon is the 15th most abundant element in the Earth\'s crust, and the fourth most abundant element in the universe by mass after hydrogen, helium, and oxygen. Carbon\'s abundance, its unique diversity of organic compounds, and its unusual ability to form polymers at the temperatures commonly encountered on Earth enables this element to serve as a common element of all known life. It is the second most abundant element in the human body by mass (about 18.5%) after oxygen. The atoms of carbon can bond together in diverse ways, r

In [ ]:
def textrank_summarizer(text, num_sent):
  doc = nlp(text)
  sentence_list = []
  for sent in doc.sents:
    sentence_list.append(sent)
  sentences = []
  for sent in doc.sents:
    doc1 = nlp(str(sent))
    sentence = [str(token) for token in doc1]
    sentences.append(sentence)
  with tf.Session() as sess:
    sess.run([tf.global_variables_initializer(), tf.tables_initializer()])
    embeddings = sess.run(embed(sentences[0]))
  embeddings = []
  with tf.Session() as sess:
    sess.run([tf.global_variables_initializer(), tf.tables_initializer()])
    for sentence in sentences:
      embeddings.append(sess.run(embed(sentence)))
  average_embedding = []
  for embedding in embeddings:
    average = np.zeros(512)
    length = len(embeddings)
    for word_embedding in embedding:
      average = average+word_embedding
    average = average/length
    average_embedding.append(average)
  average_embedding = np.array(average_embedding)
  sim_mat = np.zeros([length, length])
  for i in range(length):
    for j in range(length):
      if i != j:
        sim_mat[i][j] = cosine_similarity(average_embedding[i].reshape(1,512), average_embedding[j].reshape(1,512))[0,0]
  nx_graph = nx.from_numpy_array(sim_mat)
  scores = nx.pagerank(nx_graph)
  ranked_sentences = sorted(((scores[i],s) for i,s in enumerate(sentence_list)), reverse=True)
  final_summary = [ranked_sentences[i][1] for i in range(num_sent)]
  return final_summary

In [ ]:
import spacy
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import networkx as nx

nlp = spacy.load("en_core_web_sm")

In [ ]:
doc = nlp(text)

# Run this

In [ ]:
from flask_ngrok import run_with_ngrok
from flask import Flask, jsonify, request
app = Flask(__name__)
run_with_ngrok(app)   

@app.route('/', methods=['GET', 'POST'])
def test():
  data = request.json
  print(data['text'])
  return jsonify(data)
app.run()

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:5000/ (Press CTRL+C to quit)


 * Running on http://102c86bfd772.ngrok.io
 * Traffic stats available on http://127.0.0.1:4040


127.0.0.1 - - [02/Oct/2020 09:43:55] "POST / HTTP/1.1" 200 -


hello world


In [ ]:
text_summarizer(text, 10)

["Carbon's abundance, its unique diversity of organic compounds, and its unusual ability to form polymers at the temperatures commonly encountered on Earth enables this element to serve as a common element of all known life.",
 'All carbon allotropes are solids under normal conditions, with graphite being the most thermodynamically stable form at standard temperature and pressure.',
 'The most common oxidation state of carbon in inorganic compounds is +4, while +2 is found in carbon monoxide and transition metal carbonyl complexes.',
 'The physical properties of carbon vary widely with the allotropic form.',
 'Carbon forms a vast number of compounds, more than any other element, with almost ten million compounds described to date, and yet that number is',
 'The atoms of carbon can bond together in diverse ways, resulting in various allotropes of carbon.',
 'Three isotopes occur naturally, 12C and 13C being stable, while 14C is a radionuclide, decaying with a half-life of about 5,730 ye

In [ ]:
!pip3 install bert-embedding

     |████████████████████████████████| 13.8MB 311kB/s 
     |████████████████████████████████| 215kB 47.0MB/s 
     |████████████████████████████████| 29.6MB 141kB/s 
  Created wheel for gluonnlp: filename=gluonnlp-0.6.0-cp36-none-any.whl size=259917 sha256=125135e52b7d7d495b5e8f041f0c0b8ab47e54ab597074649369881963d6082a
  Stored in directory: /root/.cache/pip/wheels/ff/48/ac/a77c79aa416ba6dd7bf487f2280b0471034f66141617965914
Successfully built gluonnlp
ERROR: xarray 0.15.1 has requirement numpy>=1.15, but you'll have numpy 1.14.6 which is incompatible.
ERROR: umap-learn 0.4.6 has requirement numpy>=1.17, but you'll have numpy 1.14.6 which is incompatible.
ERROR: tifffile 2020.9.3 has requirement numpy>=1.15.1, but you'll have numpy 1.14.6 which is incompatible.
ERROR: tensorflow 2.3.0 has requirement numpy<1.19.0,>=1.16.0, but you'll have numpy 1.14.6 which is incompatible.
ERROR: spacy 2.2.4 has requirement numpy>=1.15.0, but you'll have numpy 1.14.6 which is incompatible.
ERROR: pl

In [ ]:
from bert_embedding import BertEmbedding

In [ ]:
embedding = BertEmbedding()

Vocab file is not found. Downloading.


In [ ]:
embedding("I am going to the park for playing with my friend")

[(['i'],
  [array([-3.25331599e-01, -3.46561611e-01,  4.29405212e-01, -3.96290034e-01,
           3.92348021e-02,  4.31209169e-02,  2.62787372e-01,  4.49371010e-01,
           8.42511803e-02, -7.80547619e-01, -7.68595338e-01,  1.82808898e-02,
           3.30514342e-01,  2.11116731e-01,  3.89601924e-02, -1.04872912e-01,
           6.49706542e-01,  3.01850110e-01, -8.97732675e-02,  6.37651980e-01,
           1.63249075e-02,  4.21480149e-01, -3.30491155e-01,  1.85020477e-01,
          -2.07559392e-02,  9.22393858e-01, -5.38871765e-01, -4.52164441e-01,
          -4.51066047e-01,  4.11571294e-01, -4.00682017e-02,  9.40975994e-02,
           4.08912599e-01,  3.52807462e-01, -5.01864612e-01, -5.43319404e-01,
          -1.77644752e-02,  1.02241397e-01, -6.06602311e-01, -2.47278795e-01,
           3.00695777e-01, -4.47480708e-01,  4.15057898e-01, -7.98903346e-01,
          -6.15273975e-02,  4.00952101e-01,  3.41679394e-01, -2.42737457e-01,
           3.38914990e-03, -6.01112694e-02, -6.85983956

In [ ]:
doc1 = nlp("Carbon is the 15th most abundant element in the Earth's crust, and the fourth most abundant element in the universe by mass after hydrogen, helium, and oxygen.")
doc2 = nlp("Carbon's abundance, its unique diversity of organic compounds, and its unusual ability to form polymers at the temperatures commonly encountered on Earth enables this element to serve as a common element of all known life.")

print(cosine_similarity(doc1.vector.reshape(1,96), doc2.vector.reshape(1,96)))

[[0.7655677]]


In [ ]:
import time

In [ ]:
=

In [ ]:
distractor_generator("bye")

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  This is separate from the ipykernel package so we can avoid doing imports until
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


['first-round', 'playoff', 'yanks']

In [ ]:
!pip install flask-ngrok